In [1]:
import pandas as pd
import tensorflow as tf


In [2]:
#File path
file_path = 'Recursos/Lottery_Pick_10_Winning_Numbers__Beginning_1987.csv'

# Read the CSV file into a DataFrame
Lottery_df = pd.read_csv(file_path)

# Display the DataFrame
Lottery_df.head()


Draw Date                                    Winning Numbers
0  09/24/2020  06 15 17 20 22 23 27 31 32 40 43 48 49 53 55 6...
1  09/25/2020  03 05 06 07 08 19 20 21 22 24 25 33 41 48 50 5...
2  09/26/2020  04 06 12 14 20 21 22 28 32 33 34 37 40 41 43 4...
3  09/27/2020  03 10 15 21 26 30 32 37 45 47 51 52 55 57 62 6...
4  09/28/2020  02 11 16 18 22 23 39 41 57 58 59 60 63 67 69 7...

In [3]:
Lottery_df['Draw Date'] = pd.to_datetime(Lottery_df['Draw Date'])
Lottery_df['Draw Month'] = Lottery_df['Draw Date'].dt.month


In [4]:
Lottery_df.head(22)

Draw Date                                    Winning Numbers  Draw Month
0  2020-09-24  06 15 17 20 22 23 27 31 32 40 43 48 49 53 55 6...           9
1  2020-09-25  03 05 06 07 08 19 20 21 22 24 25 33 41 48 50 5...           9
2  2020-09-26  04 06 12 14 20 21 22 28 32 33 34 37 40 41 43 4...           9
3  2020-09-27  03 10 15 21 26 30 32 37 45 47 51 52 55 57 62 6...           9
4  2020-09-28  02 11 16 18 22 23 39 41 57 58 59 60 63 67 69 7...           9
5  2020-09-29  04 15 18 20 21 23 24 26 29 30 34 39 40 42 49 5...           9
6  2020-09-30  01 04 07 10 16 19 28 34 36 40 46 47 51 52 59 6...           9
7  2020-10-01  05 09 21 22 23 25 31 32 33 44 45 47 50 69 70 7...          10
8  2020-10-02  05 07 14 19 28 31 36 38 47 49 51 56 59 61 66 6...          10
9  2020-10-03  06 13 22 23 26 30 31 32 34 43 44 47 49 50 53 5...          10
10 2020-10-04  03 05 06 07 10 16 17 19 20 39 45 47 50 51 53 5...          10
11 2020-10-05  01 03 11 13 14 19 22 23 24 26 28 30 35 43 44 4...          10
12 2020-10-06  02 12 13 22 25 26 28 30 31 44 53 58 62 63 65 6...          10
13 2020-10-07  01 03 10 15 17 19 22 23 25 43 46 53 60 67 68 6...          10
14 2020-10-08  07 12 14 17 22 32 33 34 35 37 40 41 43 47 53 5...          10
15 2020-10-09  12 15 20 23 25 26 28 31 35 38 48 54 57 59 66 6...          10
16 2020-10-10  05 12 16 17 18 19 26 32 39 41 48 49 53 54 59 7...          10
17 2020-10-11  01 02 05 07 08 18 26 32 35 36 41 45 49 56 60 6...          10
18 2020-10-12  03 04 07 13 16 18 21 23 32 35 40 42 43 48 49 6...          10
19 2020-10-13  03 08 15 17 18 21 25 26 34 37 39 43 44 46 48 5...          10
20 2020-10-14  06 07 12 13 23 24 25 34 35 42 44 50 51 52 59 6...          10
21 2020-10-15  07 09 16 17 20 23 28 32 33 37 42 48 55 64 66 6...          10

In [5]:
import tensorflow as tf
from sklearn.model_selection import train_test_split
from sklearn.preprocessing import StandardScaler
import numpy as np

# Preprocess data
winning_numbers = Lottery_df['Winning Numbers'].str.split(expand=True)
winning_numbers.columns = [f'Number_{i+1}' for i in range(winning_numbers.shape[1])]
Lottery_df = pd.concat([Lottery_df, winning_numbers], axis=1)
for col in winning_numbers.columns:
    Lottery_df[col] = Lottery_df[col].astype(int)

X = Lottery_df[['Draw Month'] + winning_numbers.columns.tolist()]
y = Lottery_df[winning_numbers.columns].astype(float)

X_train, X_test, y_train, y_test = train_test_split(X, y, test_size=0.2, random_state=42)
scaler = StandardScaler()
X_train = scaler.fit_transform(X_train)
X_test = scaler.transform(X_test)

# Create and compile model
model = tf.keras.models.Sequential([
    tf.keras.layers.Dense(64, activation='relu', input_shape=(X_train.shape[1],)),
    tf.keras.layers.Dense(64, activation='relu'),
    tf.keras.layers.Dense(y_train.shape[1])
])
model.compile(optimizer='adam', loss='mse', metrics=['mae'])

# Train model
history = model.fit(X_train, y_train, epochs=50, validation_split=0.2)

# Evaluate model
test_loss, test_mae = model.evaluate(X_test, y_test)
print(f"Test Loss: {test_loss}, Test MAE: {test_mae}")

# Make predictions
predictions = model.predict(X_test)
for i in range(5):
    print(f"Predicted: {predictions[i]}, True: {y_test.iloc[i].values}")


C:\Users\joesa\anaconda3\envs\Env\Lib\site-packages\keras\src\layers\core\dense.py:87: UserWarning: Do not pass an `input_shape`/`input_dim` argument to a layer. When using Sequential models, prefer using an `Input(shape)` object as the first layer in the model instead.
  super().__init__(activity_regularizer=activity_regularizer, **kwargs)


Epoch 1/50
273/273 ━━━━━━━━━━━━━━━━━━━━ 5s 7ms/step - loss: 1381.9946 - mae: 29.6637 - val_loss: 165.9235 - val_mae: 9.6468
Epoch 2/50
273/273 ━━━━━━━━━━━━━━━━━━━━ 1s 3ms/step - loss: 120.2211 - mae: 8.0308 - val_loss: 48.3002 - val_mae: 5.1258
Epoch 3/50
273/273 ━━━━━━━━━━━━━━━━━━━━ 2s 5ms/step - loss: 40.3190 - mae: 4.6700 - val_loss: 21.9183 - val_mae: 3.4720
Epoch 4/50
273/273 ━━━━━━━━━━━━━━━━━━━━ 1s 3ms/step - loss: 18.0600 - mae: 3.1766 - val_loss: 11.1858 - val_mae: 2.5041
Epoch 5/50
273/273 ━━━━━━━━━━━━━━━━━━━━ 2s 5ms/step - loss: 9.3257 - mae: 2.2869 - val_loss: 6.6686 - val_mae: 1.9497
Epoch 6/50
273/273 ━━━━━━━━━━━━━━━━━━━━ 2s 5ms/step - loss: 5.8060 - mae: 1.8262 - val_loss: 4.7044 - val_mae: 1.6423
Epoch 7/50
273/273 ━━━━━━━━━━━━━━━━━━━━ 1s 3ms/step - loss: 4.1603 - mae: 1.5499 - val_loss: 3.6478 - val_mae: 1.4422
Epoch 8/50
273/273 ━━━━━━━━━━━━━━━━━━━━ 1s 5ms/step - loss: 3.2996 - mae: 1.3742 - val_loss: 2.9367 - val_mae: 1.2930
Epoch 9/50
273/273 ━━━━━━━━━━━━━━━━━━━━ 1s 

In [6]:
import tensorflow as tf
from tensorflow.keras import layers, models

# Define the model architecture
model = models.Sequential([
    layers.Dense(64, activation='relu', input_shape=(6,)),  # Input layer with 6 features (winning numbers)
    layers.Dense(32, activation='relu'),                   # Hidden layer
    layers.Dense(1)                                        # Output layer
])

# Compile the model
model.compile(optimizer='adam', loss='mean_squared_error')

# Train the model
history = model.fit(
    x=Lottery_df[['Winning Numbers']].apply(lambda x: [int(num) for num in x.str.split()], axis=1).to_list(), 
    y=Lottery_df['Draw Month'], 
    epochs=10, 
    validation_split=0.2
)


C:\Users\joesa\anaconda3\envs\Env\Lib\site-packages\keras\src\layers\core\dense.py:87: UserWarning: Do not pass an `input_shape`/`input_dim` argument to a layer. When using Sequential models, prefer using an `Input(shape)` object as the first layer in the model instead.
  super().__init__(activity_regularizer=activity_regularizer, **kwargs)


TypeError: int() argument must be a string, a bytes-like object or a real number, not 'list'

In [7]:
import tensorflow as tf
from tensorflow.keras import layers, models

# Define the model architecture
model = models.Sequential([
    layers.Dense(64, activation='relu', input_shape=(6,)),  # Input layer with 6 features (winning numbers)
    layers.Dense(32, activation='relu'),                   # Hidden layer
    layers.Dense(1)                                        # Output layer
])

# Compile the model
model.compile(optimizer='adam', loss='mean_squared_error')

# Convert winning numbers from strings to lists of integers
winning_numbers = Lottery_df['Winning Numbers'].apply(lambda x: [int(num) for num in x.split()])

# Train the model
history = model.fit(
    x=winning_numbers.to_list(), 
    y=Lottery_df['Draw Month'], 
    epochs=10, 
    validation_split=0.2
)


C:\Users\joesa\anaconda3\envs\Env\Lib\site-packages\keras\src\layers\core\dense.py:87: UserWarning: Do not pass an `input_shape`/`input_dim` argument to a layer. When using Sequential models, prefer using an `Input(shape)` object as the first layer in the model instead.
  super().__init__(activity_regularizer=activity_regularizer, **kwargs)


ValueError: Argument `validation_split` is only supported for tensors or NumPy arrays.Found incompatible type in the input: [<class 'int'>, <class 'int'>, <class 'int'>, <class 'int'>, <class 'int'>, <class 'int'>, <class 'int'>, <class 'int'>, <class 'int'>, <class 'int'>, <class 'int'>, <class 'int'>, <class 'int'>, <class 'int'>, <class 'int'>, <class 'int'>, <class 'int'>, <class 'int'>, <class 'int'>, <class 'int'>, <class 'int'>, <class 'int'>, <class 'int'>, <class 'int'>, <class 'int'>, <class 'int'>, <class 'int'>, <class 'int'>, <class 'int'>, <class 'int'>, <class 'int'>, <class 'int'>, <class 'int'>, <class 'int'>, <class 'int'>, <class 'int'>, <class 'int'>, <class 'int'>, <class 'int'>, <class 'int'>, <class 'int'>, <class 'int'>, <class 'int'>, <class 'int'>, <class 'int'>, <class 'int'>, <class 'int'>, <class 'int'>, <class 'int'>, <class 'int'>, <class 'int'>, <class 'int'>, <class 'int'>, <class 'int'>, <class 'int'>, <class 'int'>, <class 'int'>, <class 'int'>, <clas

In [8]:
import tensorflow as tf
from tensorflow.keras import layers, models
import numpy as np

# Define the model architecture
model = models.Sequential([
    layers.Dense(64, activation='relu', input_shape=(6,)),  # Input layer with 6 features (winning numbers)
    layers.Dense(32, activation='relu'),                   # Hidden layer
    layers.Dense(1)                                        # Output layer
])

# Compile the model
model.compile(optimizer='adam', loss='mean_squared_error')

# Convert winning numbers from strings to lists of integers
winning_numbers = Lottery_df['Winning Numbers'].apply(lambda x: [int(num) for num in x.split()])

# Convert winning numbers and draw month to NumPy arrays
x_data = np.array(winning_numbers.tolist())
y_data = np.array(Lottery_df['Draw Month'])

# Train the model
history = model.fit(
    x=x_data, 
    y=y_data, 
    epochs=10, 
    validation_split=0.2
)


Epoch 1/10


ValueError: Exception encountered when calling Sequential.call().

[1mInput 0 of layer "dense_9" is incompatible with the layer: expected axis -1 of input shape to have value 6, but received input with shape (None, 20)[0m

Arguments received by Sequential.call():
  • inputs=tf.Tensor(shape=(None, 20), dtype=int32)
  • training=True
  • mask=None

In [9]:
import tensorflow as tf
from sklearn.model_selection import train_test_split
from sklearn.preprocessing import StandardScaler
import numpy as np

# Preprocess data and train/test split per month
months = Lottery_df['Draw Month'].unique()
test_losses = []
test_maes = []

for month in months:
    # Filter data for the current month
    month_data = Lottery_df[Lottery_df['Draw Month'] == month]
    
    # Preprocess data
    winning_numbers = month_data['Winning Numbers'].str.split(expand=True)
    winning_numbers.columns = [f'Number_{i+1}' for i in range(winning_numbers.shape[1])]
    month_data = pd.concat([month_data, winning_numbers], axis=1)
    for col in winning_numbers.columns:
        month_data[col] = month_data[col].astype(int)

    X = month_data[winning_numbers.columns.tolist()]
    y = month_data[winning_numbers.columns].astype(float)

    X_train, X_test, y_train, y_test = train_test_split(X, y, test_size=0.2, random_state=42)
    scaler = StandardScaler()
    X_train = scaler.fit_transform(X_train)
    X_test = scaler.transform(X_test)

    # Create and compile model
    model = tf.keras.models.Sequential([
        tf.keras.layers.Dense(64, activation='relu', input_shape=(X_train.shape[1],)),
        tf.keras.layers.Dense(64, activation='relu'),
        tf.keras.layers.Dense(y_train.shape[1])
    ])
    model.compile(optimizer='adam', loss='mse', metrics=['mae'])

    # Train model
    history = model.fit(X_train, y_train, epochs=50, validation_split=0.2, verbose=0)

    # Evaluate model
    test_loss, test_mae = model.evaluate(X_test, y_test, verbose=0)
    print(f"Month: {month}, Test Loss: {test_loss}, Test MAE: {test_mae}")
    test_losses.append(test_loss)
    test_maes.append(test_mae)

    # Make predictions (optional)
    predictions = model.predict(X_test)
    for i in range(5):
        print(f"Month: {month}, Predicted: {predictions[i]}, True: {y_test.iloc[i].values}")

# Average test loss and MAE across all months
avg_test_loss = np.mean(test_losses)
avg_test_mae = np.mean(test_maes)
print(f"Average Test Loss: {avg_test_loss}, Average Test MAE: {avg_test_mae}")



C:\Users\joesa\anaconda3\envs\Env\Lib\site-packages\keras\src\layers\core\dense.py:87: UserWarning: Do not pass an `input_shape`/`input_dim` argument to a layer. When using Sequential models, prefer using an `Input(shape)` object as the first layer in the model instead.
  super().__init__(activity_regularizer=activity_regularizer, **kwargs)


Month: 9, Test Loss: 11.935412406921387, Test MAE: 2.5902328491210938
7/7 ━━━━━━━━━━━━━━━━━━━━ 0s 15ms/step
Month: 9, Predicted: [ 9.2933655  9.042524  13.168248  13.709086  18.896296  18.996933
 22.251867  22.553835  27.624071  26.898954  30.531755  31.080202
 32.89963   33.01864   35.959747  36.111404  38.81407   38.646988
 41.099762  41.02342   44.027058  43.389114  45.088017  45.48178
 48.5864    48.62543   51.820362  50.94945   56.222427  55.78668
 60.184647  60.294537  64.561035  64.65189   69.47182   68.81986
 72.858444  72.55725   76.816696  76.34515  ], True: [11. 11. 15. 15. 17. 17. 24. 24. 29. 29. 32. 32. 34. 34. 36. 36. 41. 41.
 42. 42. 45. 45. 46. 46. 47. 47. 51. 51. 54. 54. 63. 63. 66. 66. 72. 72.
 73. 73. 80. 80.]
Month: 9, Predicted: [ 1.9861585  1.269614   3.6680882  4.081659   6.399917   6.467153
  9.415197   8.860347  11.850118  12.358999  16.566319  15.525167
 21.640207  21.433224  26.618204  25.809532  31.783754  31.51811
 35.704834  36.164158  39.848286  40.54601 

C:\Users\joesa\anaconda3\envs\Env\Lib\site-packages\keras\src\layers\core\dense.py:87: UserWarning: Do not pass an `input_shape`/`input_dim` argument to a layer. When using Sequential models, prefer using an `Input(shape)` object as the first layer in the model instead.
  super().__init__(activity_regularizer=activity_regularizer, **kwargs)


Month: 10, Test Loss: 11.13427734375, Test MAE: 2.4617371559143066
8/8 ━━━━━━━━━━━━━━━━━━━━ 0s 12ms/step
Month: 10, Predicted: [ 2.215701   2.2506452  4.713066   4.6611567  8.227412   8.0876665
 10.688342   9.85943   12.844158  12.681437  15.36553   14.923046
 18.691578  18.682468  22.124609  21.962431  26.783327  26.448896
 30.975985  31.214699  36.35134   36.21026   40.86058   40.900864
 46.037086  45.541477  49.734875  50.144375  54.04073   53.936558
 58.714397  59.353848  63.88344   63.897095  68.23338   68.32608
 72.58886   71.87334   75.62752   75.44185  ], True: [ 3.  3.  4.  4. 10. 10. 13. 13. 14. 14. 16. 16. 19. 19. 27. 27. 28. 28.
 30. 30. 41. 41. 42. 42. 49. 49. 53. 53. 54. 54. 66. 66. 67. 67. 72. 72.
 75. 75. 77. 77.]
Month: 10, Predicted: [ 6.0144663  6.202071  10.95929   10.931714  12.65601   13.698184
 15.515508  15.414365  18.71248   18.481281  22.737627  22.645748
 27.817793  28.156141  34.027428  34.507286  41.2673    41.275623
 46.175068  46.510395  52.520332  53.292

C:\Users\joesa\anaconda3\envs\Env\Lib\site-packages\keras\src\layers\core\dense.py:87: UserWarning: Do not pass an `input_shape`/`input_dim` argument to a layer. When using Sequential models, prefer using an `Input(shape)` object as the first layer in the model instead.
  super().__init__(activity_regularizer=activity_regularizer, **kwargs)


...

Month: 7, Test Loss: 11.391458511352539, Test MAE: 2.5139143466949463
8/8 ━━━━━━━━━━━━━━━━━━━━ 0s 14ms/step
Month: 7, Predicted: [ 2.6683197  2.007451   8.222648   8.794213  17.010687  16.929232
 24.697485  25.182547  31.540812  31.47287   36.185993  36.21299
 40.136097  40.11723   43.821976  44.037136  45.470623  45.71223
 48.359543  47.916058  50.798855  51.35339   54.241547  53.328465
 57.202065  56.79427   60.651302  60.059113  64.03954   63.396286
 67.42954   67.74362   70.71847   72.52241   74.25479   74.52789
 79.143654  77.43447   82.77898   81.779724 ], True: [ 1.  1.  5.  5. 11. 11. 31. 31. 33. 33. 36. 36. 38. 38. 39. 39. 40. 40.
 45. 45. 46. 46. 53. 53. 57. 57. 58. 58. 59. 59. 61. 61. 63. 63. 66. 66.
 70. 70. 79. 79.]
Month: 7, Predicted: [ 3.6146784  3.2680578  4.2319465  3.7561076  6.1282234  5.438983
  8.068647   8.463209  11.636853  11.416224  14.298836  13.967484
 16.62265   16.333094  19.307539  18.690535  21.606232  21.162848
 23.76355   24.70859   26.972792  27.79423

C:\Users\joesa\anaconda3\envs\Env\Lib\site-packages\keras\src\layers\core\dense.py:87: UserWarning: Do not pass an `input_shape`/`input_dim` argument to a layer. When using Sequential models, prefer using an `Input(shape)` object as the first layer in the model instead.
  super().__init__(activity_regularizer=activity_regularizer, **kwargs)


Month: 6, Test Loss: 13.12746810913086, Test MAE: 2.578512668609619
7/7 ━━━━━━━━━━━━━━━━━━━━ 0s 13ms/step
Month: 6, Predicted: [ 3.9401531  3.279688   5.897016   5.802388   8.4338665  8.892565
 13.493028  13.826202  19.05952   19.1695    24.231077  24.334728
 29.468393  29.13577   33.86144   34.487812  37.83436   37.95174
 41.97957   41.264946  45.068424  44.65276   47.649918  46.76534
 50.246185  49.695374  52.688667  51.465252  55.15876   55.15983
 57.158115  58.351036  61.077225  60.97106   64.23681   64.61446
 67.6662    67.594536  70.8319    70.13784  ], True: [ 4.  4.  7.  7. 10. 10. 12. 12. 23. 23. 25. 25. 30. 30. 33. 33. 37. 37.
 46. 46. 47. 47. 54. 54. 55. 55. 56. 56. 60. 60. 62. 62. 64. 64. 73. 73.
 75. 75. 76. 76.]
Month: 6, Predicted: [ 1.0752555  1.4450558  5.172699   4.8806095  8.145013   7.6739817
  9.607275   9.565248  11.66603   11.512259  13.421455  12.384327
 15.159362  14.883869  17.4014    16.634275  21.251686  20.931284
 24.390028  24.36893   27.762436  27.656874 

C:\Users\joesa\anaconda3\envs\Env\Lib\site-packages\keras\src\layers\core\dense.py:87: UserWarning: Do not pass an `input_shape`/`input_dim` argument to a layer. When using Sequential models, prefer using an `Input(shape)` object as the first layer in the model instead.
  super().__init__(activity_regularizer=activity_regularizer, **kwargs)


Month: 5, Test Loss: 8.87317943572998, Test MAE: 2.232217788696289
8/8 ━━━━━━━━━━━━━━━━━━━━ 0s 11ms/step
Month: 5, Predicted: [ 1.7098755  2.1719267  4.422582   4.7794466  7.380763   6.7620664
 10.2696905 10.734246  14.747324  14.023094  18.940641  19.132496
 23.001245  22.754803  28.35013   27.821259  31.466759  32.393665
 35.615246  34.803333  38.729908  39.26127   42.76051   41.97436
 45.325684  44.94969   47.711002  47.207092  50.809956  50.639015
 54.17119   54.054672  57.83005   57.622852  61.72443   61.569153
 64.86815   64.94402   69.321     68.44873  ], True: [ 3.  3.  4.  4.  7.  7. 12. 12. 13. 13. 18. 18. 28. 28. 30. 30. 33. 33.
 36. 36. 42. 42. 43. 43. 46. 46. 49. 49. 53. 53. 62. 62. 65. 65. 66. 66.
 70. 70. 71. 71.]
Month: 5, Predicted: [ 2.3856008  2.198874   5.21125    5.250235  10.652741  10.358726
 16.7793    16.669828  22.040384  22.878143  27.01756   27.313385
 31.251938  30.898464  35.27546   34.911434  40.117867  39.40304
 44.11023   45.04315   49.27729   49.390926

In [10]:
from tensorflow.keras.models import load_model

# Save the entire model to the "Recursos" directory
model.save('Recursos/lottery_model_per_month')

# Save only the weights to the "Recursos" directory
model.save_weights('Recursos/lottery_model_per_month_weights')


ValueError: Invalid filepath extension for saving. Please add either a `.keras` extension for the native Keras format (recommended) or a `.h5` extension. Use `model.export(filepath)` if you want to export a SavedModel for use with TFLite/TFServing/etc. Received: filepath=Recursos/lottery_model_per_month.

In [11]:
import os

# Create the "Recursos" directory if it doesn't exist
os.makedirs('Recursos', exist_ok=True)

# Save the entire model to the "Recursos" directory
model.save('Recursos/lottery_model_per_month')

# Save only the weights to the "Recursos" directory
model.save_weights('Recursos/lottery_model_per_month_weights')



ValueError: Invalid filepath extension for saving. Please add either a `.keras` extension for the native Keras format (recommended) or a `.h5` extension. Use `model.export(filepath)` if you want to export a SavedModel for use with TFLite/TFServing/etc. Received: filepath=Recursos/lottery_model_per_month.

In [12]:
# Save the entire model to the "Recursos" directory with a .h5 extension
model.save('Recursos/lottery_model_per_month.h5')


In [13]:
import tensorflow as tf
from sklearn.model_selection import train_test_split
from sklearn.preprocessing import StandardScaler, OneHotEncoder
import numpy as np

# Preprocess data (One-Hot Encoding for Month)
encoder = OneHotEncoder(sparse_output=False)
month_encoded = encoder.fit_transform(Lottery_df[['Draw Month']])
month_encoded_df = pd.DataFrame(month_encoded, columns=encoder.get_feature_names_out(['Draw Month']))
Lottery_df = pd.concat([Lottery_df, month_encoded_df], axis=1)

months = Lottery_df['Draw Month'].unique()
test_losses = []
test_maes = []

for month in months:
    month_data = Lottery_df[Lottery_df['Draw Month'] == month]
    
    winning_numbers = month_data['Winning Numbers'].str.split(expand=True)
    winning_numbers.columns = [f'Number_{i+1}' for i in range(winning_numbers.shape[1])]
    month_data = pd.concat([month_data, winning_numbers], axis=1)
    for col in winning_numbers.columns:
        month_data[col] = month_data[col].astype(int)

    X = month_data[month_encoded_df.columns.tolist() + winning_numbers.columns.tolist()]
    y = month_data[winning_numbers.columns].astype(float)

    X_train, X_test, y_train, y_test = train_test_split(X, y, test_size=0.2, random_state=42)
    scaler = StandardScaler()
    X_train = scaler.fit_transform(X_train)
    X_test = scaler.transform(X_test)

    # Create and compile model
    model = tf.keras.models.Sequential([
        tf.keras.layers.Dense(64, activation='relu', input_shape=(X_train.shape[1],)),
        tf.keras.layers.Dense(64, activation='relu'),
        tf.keras.layers.Dense(y_train.shape[1])
    ])
    model.compile(optimizer='adam', loss='mse', metrics=['mae'])

    # Train model
    history = model.fit(X_train, y_train, epochs=50, validation_split=0.2, verbose=0)

    # Evaluate model
    test_loss, test_mae = model.evaluate(X_test, y_test, verbose=0)
    print(f"Month: {month}, Test Loss: {test_loss}, Test MAE: {test_mae}")
    test_losses.append(test_loss)
    test_maes.append(test_mae)

# Average test loss and MAE across all months
avg_test_loss = np.mean(test_losses)
avg_test_mae = np.mean(test_maes)
print(f"Average Test Loss: {avg_test_loss}, Average Test MAE: {avg_test_mae}")


C:\Users\joesa\anaconda3\envs\Env\Lib\site-packages\keras\src\layers\core\dense.py:87: UserWarning: Do not pass an `input_shape`/`input_dim` argument to a layer. When using Sequential models, prefer using an `Input(shape)` object as the first layer in the model instead.
  super().__init__(activity_regularizer=activity_regularizer, **kwargs)


Month: 9, Test Loss: 11.649282455444336, Test MAE: 2.5405054092407227


C:\Users\joesa\anaconda3\envs\Env\Lib\site-packages\keras\src\layers\core\dense.py:87: UserWarning: Do not pass an `input_shape`/`input_dim` argument to a layer. When using Sequential models, prefer using an `Input(shape)` object as the first layer in the model instead.
  super().__init__(activity_regularizer=activity_regularizer, **kwargs)


Month: 10, Test Loss: 9.204477310180664, Test MAE: 2.269031286239624


C:\Users\joesa\anaconda3\envs\Env\Lib\site-packages\keras\src\layers\core\dense.py:87: UserWarning: Do not pass an `input_shape`/`input_dim` argument to a layer. When using Sequential models, prefer using an `Input(shape)` object as the first layer in the model instead.
  super().__init__(activity_regularizer=activity_regularizer, **kwargs)


...

Month: 7, Test Loss: 10.523969650268555, Test MAE: 2.414085865020752


C:\Users\joesa\anaconda3\envs\Env\Lib\site-packages\keras\src\layers\core\dense.py:87: UserWarning: Do not pass an `input_shape`/`input_dim` argument to a layer. When using Sequential models, prefer using an `Input(shape)` object as the first layer in the model instead.
  super().__init__(activity_regularizer=activity_regularizer, **kwargs)


Month: 6, Test Loss: 13.071279525756836, Test MAE: 2.5708470344543457


C:\Users\joesa\anaconda3\envs\Env\Lib\site-packages\keras\src\layers\core\dense.py:87: UserWarning: Do not pass an `input_shape`/`input_dim` argument to a layer. When using Sequential models, prefer using an `Input(shape)` object as the first layer in the model instead.
  super().__init__(activity_regularizer=activity_regularizer, **kwargs)


Month: 5, Test Loss: 10.388101577758789, Test MAE: 2.4016027450561523
Average Test Loss: 11.28003454208374, Average Test MAE: 2.4781805674235025


In [14]:
import tensorflow as tf
from sklearn.model_selection import train_test_split
from sklearn.preprocessing import StandardScaler, OneHotEncoder
import numpy as np

# Preprocess data (One-Hot Encoding for Month)
encoder = OneHotEncoder(sparse_output=False)
month_encoded = encoder.fit_transform(Lottery_df[['Draw Month']])
month_encoded_df = pd.DataFrame(month_encoded, columns=encoder.get_feature_names_out(['Draw Month']))
Lottery_df = pd.concat([Lottery_df, month_encoded_df], axis=1)

months = Lottery_df['Draw Month'].unique()
test_losses = []
test_maes = []

for month in months:
    month_data = Lottery_df[Lottery_df['Draw Month'] == month]
    
    # Split winning numbers into columns
    winning_numbers = month_data['Winning Numbers'].str.split(expand=True)
    winning_numbers.columns = [f'Number_{i+1}' for i in range(winning_numbers.shape[1])]
    month_data = pd.concat([month_data, winning_numbers], axis=1)
    for col in winning_numbers.columns:
        month_data[col] = month_data[col].astype(int)

    # Prepare features (X) and target (y) for the model
    X = month_data[month_encoded_df.columns.tolist() + winning_numbers.columns.tolist()]
    y = month_data[winning_numbers.columns].astype(float)

    # Train-test split
    X_train, X_test, y_train, y_test = train_test_split(X, y, test_size=0.2, random_state=42)

    # Scale features for better model convergence
    scaler = StandardScaler()
    X_train = scaler.fit_transform(X_train)
    X_test = scaler.transform(X_test)

    # Define the input shape for the Input layer
    input_shape = (X_train.shape[1],)

    # Create model with Input layer
    model = tf.keras.models.Sequential([
        tf.keras.layers.Input(shape=input_shape), 
        tf.keras.layers.Dense(64, activation='relu'),
        tf.keras.layers.Dense(64, activation='relu'),
        tf.keras.layers.Dense(y_train.shape[1])  # Output layer
    ])
    model.compile(optimizer='adam', loss='mse', metrics=['mae'])

    # Train the model
    history = model.fit(X_train, y_train, epochs=50, validation_split=0.2, verbose=0)

    # Evaluate the model
    test_loss, test_mae = model.evaluate(X_test, y_test, verbose=0)
    print(f"Month: {month}, Test Loss: {test_loss}, Test MAE: {test_mae}")
    test_losses.append(test_loss)
    test_maes.append(test_mae)

# Average test loss and MAE across all months
avg_test_loss = np.mean(test_losses)
avg_test_mae = np.mean(test_maes)
print(f"Average Test Loss: {avg_test_loss}, Average Test MAE: {avg_test_mae}")



Month: 9, Test Loss: 10.913045883178711, Test MAE: 2.4673149585723877
Month: 10, Test Loss: 8.757536888122559, Test MAE: 2.20487117767334
Month: 11, Test Loss: 10.819188117980957, Test MAE: 2.492387056350708
Month: 3, Test Loss: 7.858309268951416, Test MAE: 2.057488441467285
Month: 4, Test Loss: 11.634410858154297, Test MAE: 2.554725170135498
Month: 12, Test Loss: 11.066980361938477, Test MAE: 2.465146780014038
Month: 1, Test Loss: 8.480121612548828, Test MAE: 2.216261386871338
Month: 2, Test Loss: 13.572421073913574, Test MAE: 2.7090659141540527
Month: 8, Test Loss: 8.428851127624512, Test MAE: 2.1613917350769043
Month: 7, Test Loss: 9.489051818847656, Test MAE: 2.337535858154297
Month: 6, Test Loss: 11.909997940063477, Test MAE: 2.4389488697052
Month: 5, Test Loss: 7.1423492431640625, Test MAE: 2.000002384185791
Average Test Loss: 10.006022016207377, Average Test MAE: 2.342094977696737


In [15]:
# Preprocess data (One-Hot Encoding for Month)
encoder = OneHotEncoder(sparse_output=False)
month_encoded = encoder.fit_transform(Lottery_df[['Draw Month']])
month_encoded_df = pd.DataFrame(month_encoded, columns=encoder.get_feature_names_out(['Draw Month']))
Lottery_df = pd.concat([Lottery_df, month_encoded_df], axis=1)

months = Lottery_df['Draw Month'].unique()
test_losses = []
test_maes = []

for month in months:
    month_data = Lottery_df[Lottery_df['Draw Month'] == month]
    
    # Split winning numbers into columns
    winning_numbers = month_data['Winning Numbers'].str.split(expand=True)
    winning_numbers.columns = [f'Number_{i+1}' for i in range(winning_numbers.shape[1])]
    month_data = pd.concat([month_data, winning_numbers], axis=1)
    for col in winning_numbers.columns:
        month_data[col] = month_data[col].astype(int)

    # Prepare features (X) and target (y) for the model
    X = month_data[month_encoded_df.columns.tolist() + winning_numbers.columns.tolist()]
    y = month_data[winning_numbers.columns].astype(float)

    # Train-test split
    X_train, X_test, y_train, y_test = train_test_split(X, y, test_size=0.2, random_state=42)

    # Scale features for better model convergence
    scaler = StandardScaler()
    X_train = scaler.fit_transform(X_train)
    X_test = scaler.transform(X_test)

    # Define the input shape for the Input layer
    input_shape = (X_train.shape[1],)

    # Create model with Input layer
    model = tf.keras.models.Sequential([
        tf.keras.layers.Input(shape=input_shape), 
        tf.keras.layers.Dense(64, activation='relu'),
        tf.keras.layers.Dense(64, activation='relu'),
        tf.keras.layers.Dense(y_train.shape[1])  # Output layer
    ])
    model.compile(optimizer='adam', loss='mse', metrics=['mae'])

    # Train the model
    history = model.fit(X_train, y_train, epochs=150, validation_split=0.2, verbose=0)

    # Evaluate the model
    test_loss, test_mae = model.evaluate(X_test, y_test, verbose=0)
    print(f"Month: {month}, Test Loss: {test_loss}, Test MAE: {test_mae}")
    test_losses.append(test_loss)
    test_maes.append(test_mae)

# Average test loss and MAE across all months
avg_test_loss = np.mean(test_losses)
avg_test_mae = np.mean(test_maes)
print(f"Average Test Loss: {avg_test_loss}, Average Test MAE: {avg_test_mae}")



Month: 9, Test Loss: 2.215655565261841, Test MAE: 1.1035834550857544
Month: 10, Test Loss: 1.723029375076294, Test MAE: 0.9777504801750183
Month: 11, Test Loss: 1.7964140176773071, Test MAE: 1.0073411464691162
Month: 3, Test Loss: 2.031785249710083, Test MAE: 1.0304079055786133
Month: 4, Test Loss: 1.8777638673782349, Test MAE: 1.0251697301864624
Month: 12, Test Loss: 1.8240587711334229, Test MAE: 0.9999136924743652
Month: 1, Test Loss: 1.6035155057907104, Test MAE: 0.9410223364830017
Month: 2, Test Loss: 2.547745704650879, Test MAE: 1.1827833652496338
Month: 8, Test Loss: 2.0282859802246094, Test MAE: 1.052742838859558
Month: 7, Test Loss: 1.8782520294189453, Test MAE: 1.0336143970489502
Month: 6, Test Loss: 2.0687692165374756, Test MAE: 1.0658446550369263
Month: 5, Test Loss: 1.716393232345581, Test MAE: 0.9798228144645691
Average Test Loss: 1.9426390429337819, Average Test MAE: 1.033333068092664


In [16]:
# ... (your existing preprocessing and model training code)

# Create a list to hold your trained models
models = {}

for month in months:
    # ... (your existing code for training a model for each month)
    models[month] = model  # Store the trained model for the current month

# Save each model using the native Keras format
for month, model in models.items():
    model.save(f'lottery_model_month_{month}.keras') 


In [17]:
import numpy as np
import pandas as pd
import tensorflow as tf
from sklearn.model_selection import train_test_split
from sklearn.preprocessing import OneHotEncoder, StandardScaler

# ... (Your data preprocessing steps remain the same)

months = Lottery_df['Draw Month'].unique()
test_losses = []
test_maes = []
test_accuracies = []  # New list to store test accuracies

# Custom metric function for accuracy
def custom_accuracy(y_true, y_pred):
    threshold = 0.5  # You might need to adjust this threshold
    y_pred_rounded = tf.cast(tf.math.greater(y_pred, threshold), tf.float32)
    correct_predictions = tf.reduce_all(tf.equal(y_true, y_pred_rounded), axis=-1)
    return tf.reduce_mean(tf.cast(correct_predictions, tf.float32))

for month in months:
    # ... (Your feature and target preparation steps remain the same)

    # ... (Your train-test split and scaling steps remain the same)

    # Compile the model with the custom accuracy metric
    model.compile(optimizer='adam', loss='mse', metrics=['mae', custom_accuracy])

    # Train the model and store the history
    history = model.fit(X_train, y_train, epochs=150, validation_split=0.2, verbose=0)

    # Evaluate the model (now includes accuracy)
    test_loss, test_mae, test_accuracy = model.evaluate(X_test, y_test, verbose=0)
    print(f"Month: {month}, Test Loss: {test_loss}, Test MAE: {test_mae}, Test Accuracy: {test_accuracy}")
    test_losses.append(test_loss)
    test_maes.append(test_mae)
    test_accuracies.append(test_accuracy)  # Store accuracy

    # Access training loss and accuracy from history
    train_losses = history.history['loss']
    train_accuracies = history.history['custom_accuracy']
    
    print(f"Month: {month}, Training Loss: {train_losses}, Training Accuracy: {train_accuracies}")

# ... (Your averaging of test metrics remains the same)

# Average test accuracy
avg_test_accuracy = np.mean(test_accuracies)
print(f"Average Test Accuracy: {avg_test_accuracy}")


Month: 9, Test Loss: 0.04675079509615898, Test MAE: 0.09470771998167038, Test Accuracy: 0.0
Month: 9, Training Loss: [1.9379451274871826, 1.5799533128738403, 1.5337281227111816, 1.4771279096603394, 1.4628902673721313, 1.40790855884552, 1.3686140775680542, 1.3389863967895508, 1.2834635972976685, 1.2462263107299805, 1.2327207326889038, 1.1978226900100708, 1.1782500743865967, 1.0927616357803345, 1.082501769065857, 1.0654771327972412, 1.0043902397155762, 0.9774661064147949, 0.9527378678321838, 0.9131026864051819, 0.8807323575019836, 0.8551521301269531, 0.8365312814712524, 0.8024643659591675, 0.7811282277107239, 0.753455638885498, 0.7236121892929077, 0.7168514132499695, 0.689864456653595, 0.6568030118942261, 0.6378200650215149, 0.6315940618515015, 0.579505980014801, 0.5394723415374756, 0.5157600045204163, 0.49558860063552856, 0.4798443615436554, 0.4514898359775543, 0.43362486362457275, 0.4153444468975067, 0.3962972164154053, 0.3971739113330841, 0.3686063587665558, 0.34320664405822754, 0.321

In [22]:
import tensorflow as tf
from sklearn.model_selection import train_test_split
from sklearn.preprocessing import StandardScaler
import numpy as np

# Preprocess data
winning_numbers = Lottery_df['Winning Numbers'].str.split(expand=True)
winning_numbers.columns = [f'Number_{i+1}' for i in range(winning_numbers.shape[1])]
Lottery_df = pd.concat([Lottery_df, winning_numbers], axis=1)

for col in winning_numbers.columns:
    Lottery_df[col] = Lottery_df[col].astype(int)

# Features and Target
# Note: We're NOT using 'Draw Month' as a feature here.
X = Lottery_df[winning_numbers.columns.tolist()].astype(float)  
y = Lottery_df[winning_numbers.columns].astype(float)

# Train-Test Split
X_train, X_test, y_train, y_test = train_test_split(X, y, test_size=0.2, random_state=42)

# Scaling (important for neural networks)
scaler = StandardScaler()
X_train = scaler.fit_transform(X_train)
X_test = scaler.transform(X_test)

# Model Creation and Compilation
model = tf.keras.models.Sequential([
    tf.keras.layers.Dense(64, activation='relu', input_shape=(X_train.shape[1],)),
    tf.keras.layers.Dense(128, activation='relu'),
      tf.keras.layers.Dense(64, activation='relu'),   # Hidden Layer 2 (add here)
     tf.keras.layers.Dense(32, activation='relu'),   # Hidden Layer 3 (Added here) 
    
    tf.keras.layers.Dense(y_train.shape[1])        # Output layer to predict all winning numbers
])
   
model.compile(optimizer='adam', loss='mse', metrics=['mae'])

# Model Training
history = model.fit(X_train, y_train, epochs=100, validation_split=0.2)

# Model Evaluation
test_loss, test_mae = model.evaluate(X_test, y_test)
print(f"Test Loss: {test_loss}, Test MAE: {test_mae}")

# Predictions (for demonstration)
predictions = model.predict(X_test)
for i in range(5):
    print(f"Predicted: {predictions[i]}, True: {y_test.iloc[i].values}")


C:\Users\joesa\anaconda3\envs\Env\Lib\site-packages\keras\src\layers\core\dense.py:87: UserWarning: Do not pass an `input_shape`/`input_dim` argument to a layer. When using Sequential models, prefer using an `Input(shape)` object as the first layer in the model instead.
  super().__init__(activity_regularizer=activity_regularizer, **kwargs)


Epoch 1/100
273/273 ━━━━━━━━━━━━━━━━━━━━ 5s 5ms/step - loss: 1007.1569 - mae: 23.5903 - val_loss: 104.1288 - val_mae: 7.7999
Epoch 2/100
273/273 ━━━━━━━━━━━━━━━━━━━━ 2s 6ms/step - loss: 75.5170 - mae: 6.5214 - val_loss: 29.7361 - val_mae: 4.2043
Epoch 3/100
273/273 ━━━━━━━━━━━━━━━━━━━━ 1s 4ms/step - loss: 23.1680 - mae: 3.6820 - val_loss: 15.1498 - val_mae: 2.9959
Epoch 4/100
273/273 ━━━━━━━━━━━━━━━━━━━━ 1s 4ms/step - loss: 12.8286 - mae: 2.7731 - val_loss: 11.0018 - val_mae: 2.5700
Epoch 5/100
273/273 ━━━━━━━━━━━━━━━━━━━━ 1s 4ms/step - loss: 9.6891 - mae: 2.4020 - val_loss: 7.8099 - val_mae: 2.1559
Epoch 6/100
273/273 ━━━━━━━━━━━━━━━━━━━━ 1s 5ms/step - loss: 6.9258 - mae: 2.0328 - val_loss: 6.1876 - val_mae: 1.9159
Epoch 7/100
273/273 ━━━━━━━━━━━━━━━━━━━━ 1s 4ms/step - loss: 5.5968 - mae: 1.8261 - val_loss: 5.5088 - val_mae: 1.8039
Epoch 8/100
273/273 ━━━━━━━━━━━━━━━━━━━━ 1s 4ms/step - loss: 5.2234 - mae: 1.7597 - val_loss: 5.0507 - val_mae: 1.7268
Epoch 9/100
273/273 ━━━━━━━━━━━━━━━━

In [23]:
import tensorflow as tf
from sklearn.model_selection import train_test_split
from sklearn.preprocessing import StandardScaler
import numpy as np

# Preprocess data
winning_numbers = Lottery_df['Winning Numbers'].str.split(expand=True)
winning_numbers.columns = [f'Number_{i+1}' for i in range(winning_numbers.shape[1])]
Lottery_df = pd.concat([Lottery_df, winning_numbers], axis=1)

for col in winning_numbers.columns:
    Lottery_df[col] = Lottery_df[col].astype(int)

# Features and Target
# Note: We're NOT using 'Draw Month' as a feature here.
X = Lottery_df[winning_numbers.columns.tolist()].astype(float)  
y = Lottery_df[winning_numbers.columns].astype(float)

# Train-Test Split
X_train, X_test, y_train, y_test = train_test_split(X, y, test_size=0.2, random_state=42)

# Scaling (important for neural networks)
scaler = StandardScaler()
X_train = scaler.fit_transform(X_train)
X_test = scaler.transform(X_test)

# Model Creation and Compilation
model = tf.keras.models.Sequential([
    tf.keras.layers.Dense(64, activation='relu', input_shape=(X_train.shape[1],)),    
    tf.keras.layers.Dense(y_train.shape[1])        # Output layer to predict all winning numbers
])
   
model.compile(optimizer='adam', loss='mse', metrics=['mae'])

# Model Training
history = model.fit(X_train, y_train, epochs=200, validation_split=0.2)

# Model Evaluation
test_loss, test_mae = model.evaluate(X_test, y_test)
print(f"Test Loss: {test_loss}, Test MAE: {test_mae}")

# Predictions (for demonstration)
predictions = model.predict(X_test)
for i in range(5):
    print(f"Predicted: {predictions[i]}, True: {y_test.iloc[i].values}")


Epoch 1/200


C:\Users\joesa\anaconda3\envs\Env\Lib\site-packages\keras\src\layers\core\dense.py:87: UserWarning: Do not pass an `input_shape`/`input_dim` argument to a layer. When using Sequential models, prefer using an `Input(shape)` object as the first layer in the model instead.
  super().__init__(activity_regularizer=activity_regularizer, **kwargs)


273/273 ━━━━━━━━━━━━━━━━━━━━ 2s 3ms/step - loss: 1511.1851 - mae: 31.5434 - val_loss: 506.4574 - val_mae: 16.6883
Epoch 2/200
273/273 ━━━━━━━━━━━━━━━━━━━━ 1s 3ms/step - loss: 438.8381 - mae: 15.4912 - val_loss: 328.4259 - val_mae: 13.1707
Epoch 3/200
273/273 ━━━━━━━━━━━━━━━━━━━━ 1s 2ms/step - loss: 290.3975 - mae: 12.3024 - val_loss: 237.2466 - val_mae: 11.0781
Epoch 4/200
273/273 ━━━━━━━━━━━━━━━━━━━━ 1s 2ms/step - loss: 223.1444 - mae: 10.6543 - val_loss: 190.4748 - val_mae: 9.9430
Epoch 5/200
273/273 ━━━━━━━━━━━━━━━━━━━━ 1s 2ms/step - loss: 180.8162 - mae: 9.5737 - val_loss: 151.9142 - val_mae: 8.8473
Epoch 6/200
273/273 ━━━━━━━━━━━━━━━━━━━━ 1s 2ms/step - loss: 145.6148 - mae: 8.5495 - val_loss: 117.8873 - val_mae: 7.7235
Epoch 7/200
273/273 ━━━━━━━━━━━━━━━━━━━━ 1s 2ms/step - loss: 111.1813 - mae: 7.4134 - val_loss: 87.1877 - val_mae: 6.6118
Epoch 8/200
273/273 ━━━━━━━━━━━━━━━━━━━━ 1s 3ms/step - loss: 80.4341 - mae: 6.3136 - val_loss: 61.1332 - val_mae: 5.4962
Epoch 9/200
273/273 ━━━

In [24]:
model.save('lottery_predictor.h5')  # Saves in HDF5 format



In [25]:
model.save('lottery_predictor.keras')  # Change the file extension to '.keras'
print("Model saved in the new Keras format!")

Model saved in the new Keras format!


In [1]:
import tensorflow as tf

# Load the model
model_path = 'lottery_predictor.keras'
model = tf.keras.models.load_model(model_path)

# Print model summary
model.summary()

# Get input and output details
input_shape = model.input_shape
output_shape = model.output_shape
model_layers = model.layers


# ... load model ...

# Load optimizer weights separately
optimizer = tf.keras.optimizers.RMSprop()  # Or the optimizer you used
checkpoint = tf.train.Checkpoint(optimizer=optimizer, model=model)
checkpoint.restore(tf.train.latest_checkpoint(checkpoint_dir)) 


C:\Users\joesa\anaconda3\envs\Env\Lib\site-packages\keras\src\saving\saving_lib.py:415: UserWarning: Skipping variable loading for optimizer 'rmsprop', because it has 6 variables whereas the saved optimizer has 10 variables. 
  saveable.load_own_variables(weights_store.get(inner_path))


Model: "sequential_57"

┏━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━┳━━━━━━━━━━━━━━━━━━━━━━━━━━━━━┳━━━━━━━━━━━━━━━━━┓
┃ Layer (type)                         ┃ Output Shape                ┃         Param # ┃
┡━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━╇━━━━━━━━━━━━━━━━━━━━━━━━━━━━━╇━━━━━━━━━━━━━━━━━┩
│ dense_174 (Dense)                    │ (None, 64)                  │           9,024 │
├──────────────────────────────────────┼─────────────────────────────┼─────────────────┤
│ dense_175 (Dense)                    │ (None, 140)                 │           9,100 │
└──────────────────────────────────────┴─────────────────────────────┴─────────────────┘

 Total params: 36,250 (141.61 KB)

 Trainable params: 18,124 (70.80 KB)

 Non-trainable params: 0 (0.00 B)

 Optimizer params: 18,126 (70.81 KB)

In [2]:
import tensorflow as tf

# Load the model
model_path = 'lottery_predictor.keras'
model = tf.keras.models.load_model(model_path)

# Print model summary
model.summary()

# Get input and output details
input_shape = model.input_shape
output_shape = model.output_shape
model_layers = model.layers


# ... load model ...

# Load optimizer weights separately
optimizer = tf.keras.optimizers.RMSprop()  # Or the optimizer you used
checkpoint = tf.train.Checkpoint(optimizer=optimizer, model=model)
checkpoint.restore(tf.train.latest_checkpoint(checkpoint_dir)) 


Model: "sequential_57"

┏━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━┳━━━━━━━━━━━━━━━━━━━━━━━━━━━━━┳━━━━━━━━━━━━━━━━━┓
┃ Layer (type)                         ┃ Output Shape                ┃         Param # ┃
┡━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━╇━━━━━━━━━━━━━━━━━━━━━━━━━━━━━╇━━━━━━━━━━━━━━━━━┩
│ dense_174 (Dense)                    │ (None, 64)                  │           9,024 │
├──────────────────────────────────────┼─────────────────────────────┼─────────────────┤
│ dense_175 (Dense)                    │ (None, 140)                 │           9,100 │
└──────────────────────────────────────┴─────────────────────────────┴─────────────────┘

 Total params: 36,250 (141.61 KB)

 Trainable params: 18,124 (70.80 KB)

 Non-trainable params: 0 (0.00 B)

 Optimizer params: 18,126 (70.81 KB)

NameError: name 'checkpoint_dir' is not defined

In [3]:
model.summary()



Model: "sequential_57"

┏━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━┳━━━━━━━━━━━━━━━━━━━━━━━━━━━━━┳━━━━━━━━━━━━━━━━━┓
┃ Layer (type)                         ┃ Output Shape                ┃         Param # ┃
┡━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━╇━━━━━━━━━━━━━━━━━━━━━━━━━━━━━╇━━━━━━━━━━━━━━━━━┩
│ dense_174 (Dense)                    │ (None, 64)                  │           9,024 │
├──────────────────────────────────────┼─────────────────────────────┼─────────────────┤
│ dense_175 (Dense)                    │ (None, 140)                 │           9,100 │
└──────────────────────────────────────┴─────────────────────────────┴─────────────────┘

 Total params: 36,250 (141.61 KB)

 Trainable params: 18,124 (70.80 KB)

 Non-trainable params: 0 (0.00 B)

 Optimizer params: 18,126 (70.81 KB)

In [4]:
model = tf.keras.models.load_model('lottery_predictor.keras')
